In [14]:
insert_query = "INSERT IGNORE INTO default.TRANSACTION (ID, TDATE, ACCOUNT_ID, MEMO, COUNTRY, OUTFLOW, INFLOW, OWNER_ID, INSTALLMENT_NR, INSTALLMENT_TT, BILL, CREATED, UPDATED) VALUES ( %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s );"
print("DONE")

DONE


In [15]:
def find_owner(queried_name: str):
    from mysql.connector import connect, Error

    query = "SELECT * FROM OWNER"
    result = []

    try:
        with connect(
            host="127.0.0.1",
            user="root",
            password="pleasehashapasswordomg",
            database="default",
        ) as connection:
            print("[robopato] CONNECTED!", connection)
            with connection.cursor() as cursor:
                cursor.execute(query)
                query_result = cursor.fetchall()

                for item in query_result:
                    if item[1].lower() == queried_name:
                        result.append(item[0])
                        result.append(item[1])
                print("[robopato] ", result)
            print("[robopato] DONE!")
    except Error as e:
        print(e)
    finally:
        connection.close()

    return result if result else None

In [16]:
# Tests
# find_owner("daniel")[0]
# find_owner("izabely")[0]

In [17]:
def create_lists(file_name: str, bill: str):
    import re

    # Open the text file
    with open(file_name, "r", encoding="latin") as file:
        # Read the contents of the file
        contents = file.readlines()

    # Define the regex patterns
    owner_pattern = r"\s\d\s?-\s?([A-Z]+)"
    line_pattern = r"\d{2}\.\d{2}\.\d{4}.{23}.{14}.{2}\s*-?\d*\.?\d+,\d{2}\s*\d+,\d{2}"
    payment_pattern = (r"\d{2}\.\d{2}\.\d{4}PGTO.*200211(\s*-?\d*\.?\d+,\d{2})(\s*\d+,\d{2})")
    partial_invoice_line_pattern = r"\d{2}\/\d{2}.{27}.{16}.{2}\s+\s*-?\d*\.?\d+,\d{2}\s*\d+,\d{2}"

    # Lists
    current_list = None
    owner_list = []
    result = {}

    line_counter = 0
    isPartial = True

    # Find Owners
    for line in contents:
        line_counter = line_counter + 1

        found_owners = re.findall(owner_pattern, line)
        if found_owners:
            for owner_name in found_owners:
                # print(owner_name)
                list_name = f"list_{owner_name.lower()}"
                owner_list.append(list_name)
                result[list_name] = {}
                result[list_name]["owner_name"] = owner_name
                result[list_name]["owner_id"] = find_owner(owner_name.lower())[0]
                result[list_name]["bill"] = bill
                print("[robopato] owner_name", result[list_name]["owner_name"])
                print("[robopato] owner_id", result[list_name]["owner_id"])

    print("[robopato] linhas: ", line_counter)

    # Treat and create transaction lists
    counter2 = 0
    for line in contents:
        counter2 = counter2 + 1

        if re.search(owner_pattern, line):
            found_owner = re.search(owner_pattern, line)
            print(line)
            print("found_owner: ", found_owner.group(1).lower())
            owner_list = f"list_{found_owner.group(1).lower()}"
            current_list = owner_list
            result[current_list]["tlist"] = []

        else:
            if re.match(payment_pattern, line):
                result[current_list]["tlist"].append(line)
            elif re.match(line_pattern, line) or re.match(partial_invoice_line_pattern, line):
                result[current_list]["tlist"].append(line)


    # Check file pattern
    if current_list:
        sample = result[current_list]["tlist"][0]
        if re.search(line_pattern, sample):
            isPartial = False

        for listObj in result:
            result[listObj]["isPartial"] = isPartial

    print("[robopato] create_lists: DONE")

    return result

In [18]:
# Test
# create_lists("./documents/OUROCARD_VISA_INFINITE-Abr_24.txt", "Próxima Fatura")

In [19]:
def build_insert(input_dict: dict, account: int):
    from datetime import date, datetime
    from decimal import Decimal
    import re
    import hashlib

    insert_bulk = []

    # RegEx Patterns
    line_group_pattern = r"(?P<day>\d{2})\.(?P<month>\d{2})\.(?P<year>\d{4})(?:(?P<p_memo>.+PARC (?P<p_nr>\d+.)\/(?P<p_tt>\d+)\s.{12})|(?P<memo>.{37}))(?P<country>.{2})(?P<outflow>\s*-?\d*\.?\d+,\d{2})(?P<inflow>\s*\d*\.?\d+,\d{2})"
    partial_invoice_group_pattern = r"(?P<day>\d{2})\/(?P<month>\d{2})(?:(?P<p_memo>.+PARC (?P<p_nr>\d{2})\/(?P<p_tt>\d{2}).{15})|(?P<memo>.{43}))(?P<country>.{2})(?P<outflow>\s+\s*-?\d*\.?\d+,\d{2})(?P<inflow>\s*\d+,\d{2})"
    payment_pattern = r"(?P<day>\d{2})\.(?P<month>\d{2})\.(?P<year>\d{4})(?P<memo>PGTO DEBITO CONTA).*200211(?P<inflow>\s*-?\d*\.?\d+,\d{2})(?P<outflow>\s*\d+,\d{2})"

    for key in input_dict:
        if input_dict[key]["isPartial"]:
            pattern_to_use = partial_invoice_group_pattern
        else:
            pattern_to_use = line_group_pattern

        for item in input_dict[key]["tlist"]:
            # check if it is an invoice payment
            matches = re.match(payment_pattern, item)
            if matches:
                tTdate = str(
                    date(
                        int(matches.group("year")),
                        int(matches.group("month")),
                        int(matches.group("day")),
                    )
                )
                tAccount = account
                tMemo = matches.group("memo")
                tCountry = None
                tOutflow = "0.00"
                tInflow = matches.group("inflow").strip().replace(".", "").replace(",", ".").replace("-", "")
                tOwner = input_dict[key]["owner_id"]
                tInstallmentNr = None
                tInstallmentTt = None
                tBill = input_dict[key]["bill"]
                tCreated = str(datetime.now(tz=None))
                tUpdated = None
            else:
                matches = re.match(pattern_to_use, item)
                tTdate = str(
                    date(
                        # partial files will not have the year data on transactions
                        int(matches.group("year")) if pattern_to_use == line_group_pattern else datetime.now().year,
                        int(matches.group("month")),
                        int(matches.group("day")),
                    )
                )
                
                tAccount = account

                tMemo = matches.group("p_memo") if matches.group("p_memo") else matches.group("memo")
                tInstallmentNr = int(matches.group("p_nr")) if matches.group("p_nr") else None
                tInstallmentTt = int(matches.group("p_tt")) if matches.group("p_tt") else None

                tCountry = matches.group("country")
                tOutflow = matches.group("outflow").strip().replace(".", "").replace(",", ".")
                tInflow = matches.group("inflow").strip().replace(".", "").replace(",", ".")
                tOwner = input_dict[key]["owner_id"]
                tBill = input_dict[key]["bill"]

                tCreated = str(datetime.now(tz=None))
                tUpdated = None

            preHash = tTdate + tMemo + tOutflow + tInflow
            tId = hashlib.sha256(preHash.encode()).hexdigest()

            if matches.group("memo") != "Saldo Anterior":
                insert_bulk.append(
                    (
                        tId,
                        tTdate,
                        tAccount,
                        tMemo.strip(),
                        tCountry,
                        tOutflow,
                        tInflow,
                        tOwner,
                        tInstallmentNr,
                        tInstallmentTt,
                        tBill,
                        tCreated,
                        tUpdated,
                    )
                )

    return insert_bulk

In [20]:
# Test
build_insert(create_lists("./documents/OUROCARD_VISA_INFINITE-Abr_24.txt", "Próxima Fatura"), 2)

[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A37C080>
[robopato]  [1, 'DANIEL']
[robopato] DONE!
[robopato] owner_name DANIEL
[robopato] owner_id 1
[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A37C6B0>
[robopato]  [2, 'IZABELY']
[robopato] DONE!
[robopato] owner_name IZABELY
[robopato] owner_id 2
[robopato] linhas:  270
         1 - DANIEL O CARVALHO                       

found_owner:  daniel
         4 - IZABELY C NORMANDO                      

found_owner:  izabely
[robopato] create_lists: DONE


[('5cb90b993e93726adedbf10b7405f652d53930c5be578013b5390e7d96f27da4',
  '2024-03-25',
  2,
  'PGTO DEBITO CONTA',
  None,
  '0.00',
  '19249.92',
  1,
  None,
  None,
  'Próxima Fatura',
  '2024-12-21 22:34:32.910546',
  None),
 ('7188e9c14d1df302415f6ca9c340cb3c1c2e3d20dc9ffc6f80b40769d398e3d9',
  '2024-03-14',
  2,
  'EBN*XSOLLA             CURITIBA',
  'BR',
  '27.09',
  '0.00',
  1,
  None,
  None,
  'Próxima Fatura',
  '2024-12-21 22:34:32.910546',
  None),
 ('20214feeedf47b6f478073d950033ebecd4fa5960f2426a66b8ca8b3419dc8ff',
  '2024-04-06',
  2,
  'PAG*MmCultura          BRASILIA',
  'BR',
  '26.00',
  '0.00',
  1,
  None,
  None,
  'Próxima Fatura',
  '2024-12-21 22:34:32.910546',
  None),
 ('35953f06cf0254a59a6a38252aa8920562c85ffc773f281bd72193021a957c4c',
  '2024-03-16',
  2,
  'IFD*MARIANA PERDOMO CONBRASILIA',
  'BR',
  '80.79',
  '0.00',
  1,
  None,
  None,
  'Próxima Fatura',
  '2024-12-21 22:34:32.910546',
  None),
 ('c6561fbe62e5f292aff8de1bc9ab716c34652c3b12c5394ffef2

In [21]:
def db_insert(insert_bulk: list[tuple]):
    from mysql.connector import connect, Error

    try:
        with connect(
            host="127.0.0.1",
            user="root",
            password="pleasehashapasswordomg",
            database="default",
        ) as connection:
            print("CONNECTED!", connection)
            with connection.cursor() as cursor:
                cursor.executemany(insert_query, insert_bulk)
            connection.commit()
            print("DONE!")
    except Error as e:
        print(e)
    finally:
        connection.close()

In [22]:
def executor():

    from pathlib import Path

    file_path = Path(".") / "documents"

    matched_files = file_path.glob("OUROCARD*.txt")

    for file in matched_files:
        bill = file.name[:-4][23:]
        db_insert(
            build_insert(
                create_lists(file, bill), 2
                )
            )
        
    print("EXECUTOR COMPLETED.")

In [23]:
executor()

[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A384D70>
[robopato]  [1, 'DANIEL']
[robopato] DONE!
[robopato] owner_name DANIEL
[robopato] owner_id 1
[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A385460>
[robopato]  [2, 'IZABELY']
[robopato] DONE!
[robopato] owner_name IZABELY
[robopato] owner_id 2
[robopato] linhas:  270
         1 - DANIEL O CARVALHO                       

found_owner:  daniel
         4 - IZABELY C NORMANDO                      

found_owner:  izabely
[robopato] create_lists: DONE
CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A384CB0>
DONE!
[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A384C20>
[robopato]  [1, 'DANIEL']
[robopato] DONE!
[robopato] owner_name DANIEL
[robopato] owner_id 1
[robopato] CONNECTED! <mysql.connector.connection_cext.CMySQLConnection object at 0x000001E48A385640>
[rob